In [ ]:
!pip install unstructured[pdf]
# For better PDF processing
!pip install unstructured[local-inference]

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 981.5/981.5 kB 16.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.2/48.2 kB 3.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 17.6/17.6 MB 25.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.5/16.5 MB 40.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.1/48.1 kB 3.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 112.5/112.5 kB 6.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 590.6/590.6 kB 8.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 527.9/527.9 kB 17.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.6/5.6 MB 47.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 39.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.6/2.6 MB 21.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 309.7/309.7 kB 19.6 MB/s eta 0:00:00
   ━━━━━━

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 253.0/253.0 kB 7.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 472.8/472.8 kB 17.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 48.7/48.7 kB 3.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 172.3/172.3 kB 14.1 MB/s eta 0:00:00


In [ ]:
!apt-get install -y poppler-utils

Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
The following NEW packages will be installed:
  poppler-utils
0 upgraded, 1 newly installed, 0 to remove and 35 not upgraded.
Need to get 186 kB of archives.
After this operation, 697 kB of additional disk space will be used.
Get:1 http://archive.ubuntu.com/ubuntu jammy-updates/main amd64 poppler-utils amd64 22.02.0-2ubuntu0.8 [186 kB]
Fetched 186 kB in 7s (25.3 kB/s)
Selecting previously unselected package poppler-utils.
(Reading database ... 126281 files and directories currently installed.)
Preparing to unpack .../poppler-utils_22.02.0-2ubuntu0.8_amd64.deb ...
Unpacking poppler-utils (22.02.0-2ubuntu0.8) ...
Setting up poppler-utils (22.02.0-2ubuntu0.8) ...
Processing triggers for man-db (2.10.2-1) ...


In [ ]:
import os
import glob
import shutil
import pandas as pd
import kagglehub
from unstructured.partition.pdf import partition_pdf
from unstructured.chunking.title import chunk_by_title
from collections import Counter

In [ ]:
# Your existing setup
CUAD_FOLDER = kagglehub.dataset_download("konradb/atticus-open-contract-dataset-aok-beta")

# Root directory containing the 3 parts with nested folders of PDFs
pdf_root = os.path.join(CUAD_FOLDER, "CUAD_v1", "full_contract_pdf")

100%|██████████| 102M/102M [00:00<00:00, 140MB/s] 

Extracting files...


we use os.path.join to join folders => here, you give the folder names.
We use glob.glob when we want to access files of a certain pattern in directories  => basically glob.glob is used for pattern matching
os.walk()  =>  Provides a way to traverse a directory tree recursively, enabling you to visit each directory and access its subdirectories and files.

basically glob.glob is for pattern matching and os.walk is for recursive directory traversal

In [ ]:
# !rm -rf /content/pdf_data/*

In [ ]:
# Target directory where all PDFs will be copied to (create if doesn't exist)
target_pdf_dir = "pdf_data"
os.makedirs(target_pdf_dir, exist_ok=True)

# Use os.walk() instead of glob.glob for more reliable recursive traversal
all_pdf_paths = []
for dirpath, dirnames, filenames in os.walk(pdf_root):
    for filename in filenames:
        if filename.lower().endswith('.pdf'):
            full_path = os.path.join(dirpath, filename)
            all_pdf_paths.append(full_path)

print(f"Found {len(all_pdf_paths)} pdf files in nested directories.")

Found 510 pdf files in nested directories.


**PUTTING ALL PDFS INTO A SINGLE DIRECTORY**

In [ ]:
# Copy all pdfs into the target directory
for pdf_path in all_pdf_paths:
    filename = os.path.basename(pdf_path)
    target_path = os.path.join(target_pdf_dir, filename)
    shutil.copy2(pdf_path, target_path)

print(f"Copied all PDFs into: {target_pdf_dir}")

Copied all PDFs into: pdf_data


In [ ]:
# Load cleaned metadata XLSX file
metadata_df = pd.read_excel("master_clauses_cleaned-modified.xlsx")

metadata_df.head()

Filename  \
0  2ThemartComInc_19990826_10-12G_EX-10.10_670028...   
1  ABILITYINC_06_15_2020-EX-4.25-SERVICES AGREEME...   
2  ACCELERATEDTECHNOLOGIESHOLDINGCORP_04_24_2003-...   
3  ACCURAYINC_09_01_2010-EX-10.31-DISTRIBUTOR AGR...   
4  ADAMSGOLFINC_03_21_2005-EX-10.17-ENDORSEMENT A...   

                                       Document Name  \
0              CO-BRANDING AND ADVERTISING AGREEMENT   
1                                 Services Agreement   
2                            JOINT VENTURE AGREEMENT   
3  Multiple LINAC and Multi-Modality Distributor ...   
4                              ENDORSEMENT AGREEMENT   

                                             Parties Agreement Date  \
0  I-ESCROW, INC. ("i-Escrow" ); 2THEMART.COM, IN...     21-06-1999   
1  [ * * * ] ("Provider"); TELCOSTAR PTE, LTD.; A...     10-01-2019   
2  Collectible Concepts Group, Inc. ("CCGI"); Piv...            NaN   
3  ACCURAY INCORPORATED, ("Accuray"); SIEMENS AKT...     06-08-2010   
4  TOM WATSON ("CONSULTANT"); ADAMS GOLF, LTD. ("...     13-01-2005   

  Effective Date Expiration Date       Renewal Term  \
0     21-06-1999      21-06-2000  Successive 1 year   
1     11-01-2019      31-12-2020                NaN   
2     03-01-2003      28-02-2004                NaN   
3     06-08-2010       perpetual                NaN   
4     09-01-2004        []-[]-[]                NaN   

  Notice Period To Terminate Renewal Governing Law  \
0                            30 days    California   
1                                NaN        Israel   
2                                NaN  Pennsylvania   
3                                NaN       Germany   
4                                NaN        Kansas   

                   Competitive Restriction Exception  ...  \
0                                                 No  ...   
1                                                 No  ...   
2                                                 No  ...   
3                                                 No  ...   
4  Yes - ["The parties expressly agree that CONSU...  ...   

  Unlimited/All-You-Can-Eat-License Irrevocable Or Perpetual License  \
0                                No                               No   
1                                No                               No   
2                                No                               No   
3                                No                               No   
4                                No                               No   

                           Post-Termination Services  \
0  Yes - ['Notwithstanding the foregoing, unless ...   
1                                                 No   
2                                                 No   
3  Yes - ['Furthermore, each of the parties agree...   
4                                                 No   

                                        Audit Rights  \
0  Yes - ["Such inspection shall be at 2TheMart's...   
1                                                 No   
2  Yes - ['All books and records of every kind an...   
3                                                 No   
4                                                 No   

                                  Uncapped Liability  \
0  Yes - ['EXCEPT IN THE EVENT OF A BREACH OF SEC...   
1                                                 No   
2                                                 No   
3  Yes - ['WITHOUT AFFECTING STRICT PRODUCT LIABI...   
4                                                 No   

                                    Cap On Liability Liquidated Damages  \
0  Yes - ['EXCEPT IN THE EVENT OF A BREACH OF SEC...                 No   
1                                                 No                 No   
2                                                 No                 No   
3  Yes - ["This will be Accuray's sole and exclus...                 No   
4                                                 No                 No   

                         

In [ ]:
# Parameters
max_characters = 1000
new_after_n_chars = 800
combine_text_under_n_chars = 100

# Create metadata lookup
metadata_dict = {}          # O(1) lookup

# For each row, iterrows() returns a tuple containing two elements: The index of the row and the data of the row as a Pandas Series object.
for idx, row in metadata_df.iterrows():
    filename_key = row['Filename'].lower().replace('.pdf', '')
    metadata_dict[filename_key] = row.to_dict()

print(f"Metadata entries loaded: {len(metadata_dict)}")
print(metadata_dict)       # dict key=filename and value=the entire row

Metadata entries loaded: 510
{'2themartcominc_19990826_10-12g_ex-10.10_6700288_ex-10.10_co-branding agreement_ agency agreement': {'Filename': '2ThemartComInc_19990826_10-12G_EX-10.10_6700288_EX-10.10_Co-Branding Agreement_ Agency Agreement.pdf', 'Document Name': 'CO-BRANDING AND ADVERTISING AGREEMENT', 'Parties': 'I-ESCROW, INC. ("i-Escrow" ); 2THEMART.COM, INC. ("2TheMart")', 'Agreement Date': '21-06-1999', 'Effective Date': '21-06-1999', 'Expiration Date': '21-06-2000', 'Renewal Term': 'Successive 1 year', 'Notice Period To Terminate Renewal': '30 days', 'Governing Law': 'California', 'Competitive Restriction Exception': 'No', 'Non-Compete': 'Yes - ["i-Escrow shall not run banner advertisements on the Co-Branded Site for any of 2TheMart\'s competitors."]', 'Exclusivity': 'No', 'No-Solicit Of Customers': 'No', 'No-Solicit Of Employees': 'No', 'Non-Disparagement': 'No', 'Termination For Convenience': 'No', 'Rofr/Rofo/Rofn': 'No', 'Change Of Control': 'Yes - ["If a majority of the equi

**DEBUGGING-1**

In [ ]:
!find /content/pdf_data -type f -iname "*.pdf" | wc -l

510


In [ ]:
contract_dir = "/content/pdf_data"

# DEBUG: Check that all PDFs (case-insensitive) are picked up
pdf_paths = [os.path.join(contract_dir, f)
             for f in os.listdir(contract_dir)
             if f.lower().endswith('.pdf')]

print(f"Number of PDF files in {contract_dir}: {len(pdf_paths)}")

Number of PDF files in /content/pdf_data: 510


In [ ]:
# Build lists for filenames and file paths
filename_list = []
filepath_dict = {}

for file_path in pdf_paths:
    filename = os.path.basename(file_path).lower().replace('.pdf', '')
    filename_list.append(filename)
    filepath_dict[filename] = file_path  # full path for chunking

filename_list.sort()
print(f"Unique PDF filenames found: {len(filename_list)}")
print(filename_list)        # prints sorted list of the filenames
print(filepath_dict)      # returns unsorted dict of key=filename andfilepath

Unique PDF filenames found: 510
['2themartcominc_19990826_10-12g_ex-10.10_6700288_ex-10.10_co-branding agreement_ agency agreement', 'abilityinc_06_15_2020-ex-4.25-services agreement', 'acceleratedtechnologiesholdingcorp_04_24_2003-ex-10.13-joint venture agreement', 'accurayinc_09_01_2010-ex-10.31-distributor agreement', 'adamsgolfinc_03_21_2005-ex-10.17-endorsement agreement', 'adaptimmunetherapeuticsplc_04_06_2017-ex-10.11-strategic alliance agreement', 'adianutrition,inc_04_01_2005-ex-10.d2-reseller agreement', 'adma biomanufacturing, llc -  amendment 3 to manufacturing agreement', 'adurobiotech,inc_06_02_2020-ex-10.7-consulting agreement', 'adurobiotech,inc_06_02_2020-ex-10.7-consulting agreement(1)', 'afsalabancorpinc_08_01_1996-ex-1.1-agency agreement', 'agapeatpcorp_20191202_10-ka_ex-10.1_11911128_ex-10.1_supply agreement', 'aimmunetherapeuticsinc_20200205_8-k_ex-10.3_11967170_ex-10.3_development agreement', 'airspannetworksinc_04_11_2000-ex-10.5-distributor agreement', 'airtech

**DEBUGGING-2**

In [ ]:
# Quick diagnostic to understand filename differences

def analyze_filename_patterns():
    dataset_files = filename_list
    metadata_files = [f.lower().replace('.pdf', '') for f in metadata_df['Filename']]

    exact_matches = set(dataset_files) & set(metadata_files)
    only_in_dataset = set(dataset_files) - set(metadata_files)
    only_in_metadata = set(metadata_files) - set(dataset_files)

    print(f"\nMatching analysis:")
    print(f"Exact matches: {len(exact_matches)}")
    print(f"Only in dataset: {len(only_in_dataset)}")
    print(f"Only in metadata: {len(only_in_metadata)}")

    if only_in_dataset:
        print(f"\nExamples of dataset-only files:")
        for i, name in enumerate(sorted(only_in_dataset)[:5]):
            print(f"  {i+1}. {name}")

    if only_in_metadata:
        print(f"\nExamples of metadata-only files:")
        for i, name in enumerate(sorted(only_in_metadata)[:5]):
            print(f"  {i+1}. {name}")

# Run it
analyze_filename_patterns()


Matching analysis:
Exact matches: 510
Only in dataset: 0
Only in metadata: 0


**CHUNKING OF PDFS AND APPENDING TO METADATA**

In [ ]:
chunks_with_metadata = []
processed_count = 0

for i, file_name in enumerate(filename_list):
    print(f"\n=== Processing {i+1}/{len(filename_list)}: {file_name} ===")

    if file_name not in metadata_dict:
        print(f"Skipping {file_name} — No metadata found")
        continue

    pdf_path = filepath_dict[file_name]

    # strategy="hi-res" is too slow and hangs on some pdfs, so going for a simpler strategy
    try:
        elements = partition_pdf(
            filename=pdf_path,
            strategy="fast",  # Changed from hi_res to fast
            chunking_strategy="by_title",
            max_characters=max_characters,
            new_after_n_chars=new_after_n_chars,
            combine_text_under_n_chars=combine_text_under_n_chars
        )

        # Process elements
        chunk_count = 0
        for element in elements:
            if not element.text.strip():
                continue

            enriched_doc = {
                "text": element.text,
                "metadata": {
                    **metadata_dict[file_name],
                    "Filename": file_name,
                    "element_type": str(type(element).__name__),
                    "chunk_type": "unstructured_fast",
                    "page_number": getattr(element.metadata, 'page_number', None),
                    "coordinates": getattr(element.metadata, 'coordinates', None)
                }
            }
            chunks_with_metadata.append(enriched_doc)
            chunk_count += 1

        print(f"✅ Success! Generated {chunk_count} chunks")
        processed_count += 1

    except Exception as e:
        print(f"❌ Error processing {file_name}: {str(e)}")

    # Progress update every 10 files
    if (i + 1) % 10 == 0:
        print(f"\n📊 Progress: {processed_count}/{i+1} files processed successfully")

print(f"\nFINISHED: {processed_count}/{len(filename_list)} files processed")
print(f"Total chunks generated: {len(chunks_with_metadata)}")


=== Processing 1/510: 2themartcominc_19990826_10-12g_ex-10.10_6700288_ex-10.10_co-branding agreement_ agency agreement ===
✅ Success! Generated 42 chunks

=== Processing 2/510: abilityinc_06_15_2020-ex-4.25-services agreement ===
✅ Success! Generated 40 chunks

=== Processing 3/510: acceleratedtechnologiesholdingcorp_04_24_2003-ex-10.13-joint venture agreement ===
✅ Success! Generated 13 chunks

=== Processing 4/510: accurayinc_09_01_2010-ex-10.31-distributor agreement ===
✅ Success! Generated 157 chunks

=== Processing 5/510: adamsgolfinc_03_21_2005-ex-10.17-endorsement agreement ===
✅ Success! Generated 38 chunks

=== Processing 6/510: adaptimmunetherapeuticsplc_04_06_2017-ex-10.11-strategic alliance agreement ===
✅ Success! Generated 127 chunks

=== Processing 7/510: adianutrition,inc_04_01_2005-ex-10.d2-reseller agreement ===
✅ Success! Generated 28 chunks

=== Processing 8/510: adma biomanufacturing, llc -  amendment 3 to manufacturing agreement ===
✅ Success! Generated 17 chunks

In [ ]:
import pickle

# Save the chunks_with_metadata list to a .pkl file
with open("chunks_with_metadata.pkl", "wb") as f:
    pickle.dump(chunks_with_metadata, f)

print("✅ Saved all chunks to chunks_with_metadata.pkl")


✅ Saved all chunks to chunks_with_metadata.pkl
